In [1]:
import geopandas as gpd
import pandas as pd
from shapely.ops import unary_union
import numpy as np
import geojson
import folium
from folium import Choropleth
from branca.colormap import linear
from statsmodels.tsa.arima.model import ARIMA
import itertools
import warnings
from statsmodels.tools.sm_exceptions import ValueWarning

In [2]:
# Load the shapefile
gdf = gpd.read_file("../data/GDA2020/")
gdf = gdf.to_crs(epsg=4326)

# Check the data
print(gdf["geometry"].head())

0    POLYGON ((146.65061 -36.94496, 146.68449 -36.9...
1    POLYGON ((144.99137 -37.80959, 144.99254 -37.8...
2    POLYGON ((144.88854 -37.75546, 144.88854 -37.7...
3    POLYGON ((146.35535 -37.69944, 146.35751 -37.6...
4    POLYGON ((145.638 -37.28417, 145.64233 -37.279...
Name: geometry, dtype: geometry


In [3]:
def pre_process_excel(df):
    # Drop the first column
    df = df.iloc[:, 1:]

    # Set the current first row as the column names
    df.columns = df.iloc[0]  # Use the first row as column names
    df = df.drop(df.index[0])  # Drop the row that became column headers

    # Reset the index
    df = df.reset_index(drop=True)
    
    columns = ["Suburb"]

    for i in range(1, len(df.columns)):
        if pd.isna(df.columns[i]):
            columns.append(df.columns[i-1] + " median")  # Use the previous column if current is NaN
        else:
            columns.append(df.columns[i] + " count")  # Use the current column otherwise

    # Assign the new columns list to the DataFrame
    df.columns = columns

    df = df.iloc[1:]
    
    return df

In [4]:
# Create rename dictionary for union with gdf DataFrame
rename_dict = {"CBD": ["Melbourne"], "St Kilda Rd": ["St Kilda"], "West St Kilda": ["St Kilda West"], "East St Kilda": ["St Kilda East"], 
               "Mt Eliza": ["Mount Eliza"], "Mt Martha": ["Mount Martha"], "Newcombe": ["Newcomb"], "Bendigo East": ["East Bendigo"], 
               "East Hawthorn": ["Hawthorn East"], "East Brunswick": ["Brunswick East"], "West Brunswick": ["Brunswick West"], 
               "Ballarat": ['Ballarat Central', 'Ballarat East', 'Ballarat North'], 
               "Wanagaratta": ['East Wangaratta', 'North Wangaratta', 'Wangaratta', 'Wangaratta South'],
               "Yarra Ranges": ["Lilydale", "Belgrave", "Healesville", "Warburton", "Mount Dandenong",
                "Olinda", "Monbulk", "Yarra Glen", "Seville", "Coldstream",
                "Wandin North", "Kilsyth", "Chirnside Park"]}

def process_geometry(df, rows_with_dash, rows_without_dash):
    df['new_geom'] = np.nan
    df['new_geom'] = df['new_geom'].astype(object)

    # Add geometry for union suburbs
    combined_geom_mapping = {}

    for elem in rows_with_dash:
        lst = elem.split("-")
        temp_geom = []
        for item in lst:
            if item not in list(gdf["LOC_NAME"]):
                item = rename_dict.get(item, [item])[0]
            geom = gdf[gdf["LOC_NAME"] == item]["geometry"]
            if not geom.empty:
                temp_geom.append(geom.values[0])
            else:
                print(f"Warning: No geometry found for {item}")
        if temp_geom:  # Only add if we have at least one geometry
            combined_geom_mapping[elem] = unary_union(temp_geom)
        else:
            print(f"No geometries to combine for '{elem}'")

    # Assign combined geometries to the appropriate rows in df
    for elem, geom in combined_geom_mapping.items():
        if elem in df['Suburb'].values:
            df.loc[df['Suburb'] == elem, 'new_geom'] = geom
        else:
            print(f"Row with identifier '{elem}' not found in df.")

    #Add geometry for single suburb
    single_geom_mapping = {}

    for item in rows_without_dash:
        if item != "Group Total":
            elements = []
            temp_geom = []
            if item not in list(gdf["LOC_NAME"]):
                elements = rename_dict[item]
            else:
                elements = [item]
            for elem in elements:
                geom = gdf[gdf["LOC_NAME"] == elem]["geometry"]
                if not geom.empty:
                    temp_geom.append(geom.values[0])
                else:
                    print(f"Warning: No geometry found for {elem}")
            single_geom_mapping[item] = unary_union(temp_geom)

    # Assign single geometries to the appropriate rows in df
    for item, geom in single_geom_mapping.items():
        if item in df['Suburb'].values:
            df.loc[df['Suburb'] == item, 'new_geom'] = geom
        else:
            print(f"Row with identifier '{item}' not found in df.")
    
    return df
    
    
def process_for_visualisation(df):
    # Check if any element in the 'Suburb' column contains the '-' symbol
    contains_dash = df['Suburb'].str.contains('-', na=False)

    # Display rows where the 'Suburb' column contains '-'
    rows_with_dash = list(df["Suburb"][contains_dash])
    rows_without_dash = df["Suburb"][~contains_dash]
    
    df_with_geom = process_geometry(df, rows_with_dash, rows_without_dash)
    
    return df_with_geom

def visualisation_mar_2024_median(df, house_type, save = True, display = False):
    # Create a map centered on Victoria
    m = folium.Map(location=[-37.4713, 144.7852], zoom_start=7)

    latest_median = 'Mar 2024 median'

    df[latest_median] = pd.to_numeric(df[latest_median], errors='coerce')

    # Create a colormap
    colormap = linear.Spectral_11.scale(df[latest_median].min(), df[latest_median].max())

    # Convert geometries to GeoJSON format with properties
    geojson_features = []
    for index, row in df.dropna(subset=['new_geom', latest_median]).iterrows():
        feature = geojson.Feature(
            geometry=row['new_geom'],
            properties={
                'value': row[latest_median]
            }
        )
        geojson_features.append(feature)

    # Create a GeoJSON feature collection
    feature_collection = geojson.FeatureCollection(geojson_features)

    # Add GeoJSON to the map with color based on latest_median
    folium.GeoJson(
        feature_collection,
        style_function=lambda feature: {
            'fillColor': colormap(feature['properties']['value']),
            'color': 'black',
            'weight': 1,
            'fillOpacity': 0.6
        }
    ).add_to(m)

    # Add a color legend to the map
    colormap.add_to(m)

    # Add markers for the top 10 suburbs
    df[latest_median] = pd.to_numeric(df[latest_median], errors='coerce')
    top_10_suburbs = df.dropna(subset=['new_geom', latest_median]).nlargest(10, latest_median)

    for index, row in top_10_suburbs.iterrows():
        # Calculate the centroid of the suburb's geometry for marker placement
        centroid = row['new_geom'].centroid
        popup_text = f"Suburb: {row['Suburb']}<br>Mar 2024 median: {row[latest_median]}"
        
        # Add marker to the map
        folium.Marker(
            location=[centroid.y, centroid.x],
            popup=popup_text
        ).add_to(m)
    
    if save:
        m.save(f"../plots/march 2024 median rent/{house_type}.html")

    # Show the map
    if display:
        return m

In [5]:
def process_for_prediction(df):
    # Extract suburb and median columns
    median_columns = ["Suburb"]
    for col in df.columns:
        if "median" in col:
            median_columns.append(col)

    median_data = df[median_columns].dropna(how='all', subset=median_columns)

    # Reshape the data from wide to long format
    df_long = pd.melt(median_data, id_vars=['Suburb'], var_name='date', value_name='median_rental_price')

    # Remove the word 'median' from the 'date' column
    df_long['date'] = df_long['date'].str.replace(' median', '', regex=False)

    # Convert the cleaned 'date' column to datetime
    df_long['date'] = pd.to_datetime(df_long['date'], format='%b %Y', errors='coerce')
    
    return df_long

In [6]:
# Suppress warnings
warnings.filterwarnings('ignore', category=UserWarning)
warnings.filterwarnings('ignore', category=pd.errors.SettingWithCopyWarning)
warnings.filterwarnings('ignore', category=ValueWarning)
warnings.filterwarnings('ignore', category=FutureWarning)

def split_suburbs(final_df):
    # Initialize a list to store the updated rows
    updated_rows = []

    # Loop through each row in the final_df
    for index, row in final_df.iterrows():
        suburb = row['Suburb']
        
        # Check if the suburb is in rows_with_dash 
        if "-" in suburb:
            # Split the suburb by the hyphen
            split_suburbs = suburb.split("-")
            
            # For each split suburb, create a new row with the same predictions
            for split_suburb in split_suburbs:
                # Create a copy of the row and update the Suburb name
                new_row = row.copy()
                new_row['Suburb'] = split_suburb.strip()  # Strip spaces if any
                updated_rows.append(new_row)
        else:
            # If not in rows_with_dash, keep the row as is
            updated_rows.append(row)

    # Create a new DataFrame with the updated rows
    final_split_df = pd.DataFrame(updated_rows)

    # Sort the DataFrame by Suburb name to keep it organized
    final_split_df = final_split_df.sort_values(by='Suburb').reset_index(drop=True)

    return final_split_df

def future_median_predict(df):
    # Initialize results list
    results = []

    # Define ranges for ARIMA parameters
    p_values = range(0, 6)
    d_values = [0, 1]
    q_values = [0, 1, 2, 3]
    pdq_combinations = list(itertools.product(p_values, d_values, q_values))

    # Loop through each suburb in the dataset
    for suburb in df['Suburb'].unique():
        
        suburb_df = df[df['Suburb'] == suburb].copy()
        
        # Convert median_rental_price to numeric and drop NaNs
        suburb_df['median_rental_price'] = pd.to_numeric(suburb_df['median_rental_price'], errors='coerce')
        suburb_df = suburb_df.dropna(subset=['median_rental_price'])
        
        # Convert date column to datetime and set as index
        suburb_df['date'] = pd.to_datetime(suburb_df['date'], errors='coerce')
        suburb_df = suburb_df.dropna(subset=['date'])
        suburb_df.set_index('date', inplace=True)

        # Ensure suburb has at least 10 entries before fitting the model
        if len(suburb_df) < 10:
            forecast_yearly = pd.DataFrame({'Suburb': [suburb] * 4}, index=[f'2025', f'2026', f'2027', f'2028'])
            forecast_yearly['forecasted_median_rental_price'] = np.nan
            results.append(forecast_yearly)
            continue

        # Log transform to stabilize variance
        suburb_df['log_median_rental_price'] = np.log(suburb_df['median_rental_price'] + 1)  # Add 1 to avoid log(0)

        # Initialize variables to store the best model information
        best_aic = np.inf
        best_order = None
        best_model_fit = None
        
        # Perform grid search for ARIMA parameters (p, d, q)
        for (p, d, q) in pdq_combinations:
            try:
                model = ARIMA(suburb_df['log_median_rental_price'], order=(p, d, q))
                model_fit = model.fit()
                
                if model_fit.aic < best_aic:
                    best_aic = model_fit.aic
                    best_order = (p, d, q)
                    best_model_fit = model_fit
            except:
                continue

        if best_model_fit:
            # Forecast for 48 months (4 years: 2025 to 2028)
            forecast_steps = 48
            forecast = best_model_fit.forecast(steps=forecast_steps)

            # Inverse log transformation
            forecast = np.exp(forecast) - 1

            # Ensure no negative values in forecast
            forecast[forecast < 0] = 0
            
            # Create date range and DataFrame for the forecast
            forecast_dates = pd.date_range(start=suburb_df.index[-1], periods=forecast_steps + 1, freq='MS')[1:]
            forecast_df = pd.DataFrame({'date': forecast_dates, 'forecasted_median_rental_price': forecast})
            forecast_df.set_index('date', inplace=True)

            # Resample monthly forecast to yearly and limit to 2025-2028
            forecast_yearly = forecast_df.resample('YS').mean()
            forecast_yearly = forecast_yearly.loc['2025':'2028']
            forecast_yearly['Suburb'] = suburb
            results.append(forecast_yearly)

    # Combine all suburb forecasts
    forecast_df_combined = pd.concat(results)

    # Pivot the table to have 'Suburb' as columns and dates as rows
    final_results = forecast_df_combined.pivot_table(values='forecasted_median_rental_price', index=forecast_df_combined.index, columns='Suburb')
    
    # Transpose and reset the index for the final result
    final_df = final_results.T.reset_index()

    # Rename the columns for clarity
    final_df = final_df.rename(columns={'index': 'Suburb'})

    # Reorder the DataFrame columns to have 'Suburb' first, followed by dates
    columns_order = ['Suburb'] + [col for col in final_df.columns if col != 'Suburb']
    final_df = split_suburbs(final_df[columns_order])
    
    return final_df

In [197]:
# Load the Excel File
xls = pd.ExcelFile("../data/hist_rent_2024.xlsx")

# Set of house types
house_types = {"1 bedroom flat", "2 bedroom flat", "3 bedroom flat", "2 bedroom house", "3 bedroom house", "4 bedroom house"}

# Corresponding dictionary with dataframes
house_dict = {house_type:None for house_type in house_types}

for item in house_types: 
    house_dict[item] = pd.read_excel(xls, item)

# Process the dataframes
for house_type, df in house_dict.items():
    
    # Raw process to get the desired format
    raw_processed_df = pre_process_excel(df)
    
    # Visualise the data
    visualisation_processed_df = process_for_visualisation(raw_processed_df)
    
    visualisation_mar_2024_median(visualisation_processed_df, house_type)
    
    # Predict the median rental price
    prediction_processed_df = process_for_prediction(raw_processed_df)
    
    future_df = future_median_predict(prediction_processed_df)
    
    future_df.to_csv(f"../data/curated/future_median/{house_type}.csv")
    

In [7]:
import pandas as pd

xls = pd.ExcelFile("../data/hist_rent_2024.xlsx")
historical_rent = pd.read_excel(xls, "All properties")

df = pre_process_excel(historical_rent)

visualise_df = process_for_visualisation(df)

visualise_df.head()


Suburb Mar 2000 count Mar 2000 median  \
1  Albert Park-Middle Park-West St Kilda           1143             260   
2                               Armadale            733             200   
3                          Carlton North            864             260   
4                      Carlton-Parkville           1303             251   
5                        CBD-St Kilda Rd           2132             320   

  Jun 2000 count Jun 2000 median Sep 2000 count Sep 2000 median  \
1           1134             260           1177             270   
2            737             200            738             205   
3            814             260            799             265   
4           1278             260           1280             260   
5           2264             320           2358             320   

  Dec 2000 count Dec 2000 median Mar 2001 count  ... Mar 2023 median  \
1           1178             275           1208  ...             545   
2            739             210            718  ...             490   
3            736             270            718  ...             620   
4           1301             260           1260  ...             500   
5           2361             320           2591  ...             550   

  Jun 2023 count Jun 2023 median Sep 2023 count Sep 2023 median  \
1            740             550            730             600   
2            687             500            639             525   
3            495             630            467             650   
4           2755             530           2687             550   
5          13505             580          13552             600   

  Dec 2023 count Dec 2023 median Mar 2024 count Mar 2024 median  \
1            720             600            671             650   
2            594             560            566             560   
3            418             670            384             680   
4           2662             550           2543             570   
5          13564             620          13582             640   

                                            new_geom  
1  POLYGON ((144.97073165300392 -37.8535929351785...  
2  POLYGON ((145.00893190485596 -37.8582340928225...  
3  POLYGON ((144.9588916860838 -37.78894093996848...  
4  POLYGON ((144.9588367869097 -37.79984841703238...  
5  POLYGON ((144.9707814169981 -37.85356665018178...  

[5 rows x 196 columns]

In [8]:
visualisation_mar_2024_median(visualise_df, "All properties", save = True, display = True)

In [9]:
df_long = process_for_prediction(df)

final_df = future_median_predict(df_long)

final_df.head()

date       Suburb  2025-01-01 00:00:00  2026-01-01 00:00:00  \
0      Abbotsford           678.839170           681.048574   
1     Albert Park           706.848215           706.962547   
2       Alfredton           508.693576           581.643705   
3      Alphington           530.751586           530.747432   
4          Altona           792.984808           967.991348   

date  2027-01-01 00:00:00  2028-01-01 00:00:00  
0              681.150854           681.155291  
1              706.964324           706.964406  
2              658.701188           708.587987  
3              530.747396           530.747396  
4             1096.721871          1157.728979

In [11]:
final_df.loc[final_df["Suburb"] == "CBD"]

date Suburb  2025-01-01 00:00:00  2026-01-01 00:00:00  2027-01-01 00:00:00  \
35      CBD           528.336381           539.228352           540.684859   

date  2028-01-01 00:00:00  
35             538.329317